In [1]:
def basis_holomorphic_differentials_degree(f, m, p):
    r = f.degree()
    delta = GCD(r, m)
    Rx.<x> = PolynomialRing(GF(p))
    Rxy.<x, y> = PolynomialRing(GF(p), 2)
    Fxy = FractionField(Rxy)
    #########basis of holomorphic differentials and de Rham
                
    basis_holo = []
    degrees0 = {}
    k = 0
        
    for j in range(1, m):
        for i in range(1, r):
            if (r*j - m*i >= delta):
                basis_holo += [Fxy(x^(i-1)/y^j)]
                degrees0[k] = (i-1, j)
                k = k+1
                    
    return(basis_holo, degrees0)

def holomorphic_differentials_basis(f, m, p):
        basis_holo, degrees0 = basis_holomorphic_differentials_degree(f, m, p)
        return basis_holo
        
def degrees_holomorphic_differentials(f, m, p):
    basis_holo, degrees0 = basis_holomorphic_differentials_degree(f, m, p)
    return degrees0
    
def basis_de_rham_degrees(f, m, p):
    r = f.degree()
    delta = GCD(r, m)
    Rx.<x> = PolynomialRing(GF(p))
    Rxy.<x, y> = PolynomialRing(GF(p), 2)
    Fxy = FractionField(Rxy)
    basis_holo = holomorphic_differentials_basis(f, m, p)
    basis = []
    for k in range(0, len(basis_holo)):
        basis += [(basis_holo[k], Rx(0))]

    ## non-holomorphic elts of H^1_dR
    t = len(basis)
    degrees0 = {}
    degrees1 = {}
    for j in range(1, m):
        for i in range(1, r):
            if (r*(m-j) - m*i >= delta): 
                s = Rx(m-j)*Rx(x)*Rx(f.derivative()) - Rx(m)*Rx(i)*f
                psi = Rx(cut(s, i))
                basis += [(Fxy(psi/y^j), Fxy(m*y^(m-j)/x^i))]
                degrees0[t] = (psi.degree(), j)
                degrees1[t] = (-i, m-j)
                t += 1
    return basis, degrees0, degrees1

def de_rham_basis(f, m, p):
    basis, degrees0, degrees1 = basis_de_rham_degrees(f, m, p)
    return basis

def degrees_de_rham0(f, m, p):
    basis, degrees0, degrees1 = basis_de_rham_degrees(f, m, p)
    return degrees0

def degrees_de_rham1(f, m, p):
    basis, degrees0, degrees1 = basis_de_rham_degrees(f, m, p)
    return degrees1    


class superelliptic:
    
    def __init__(self, f, m, p):
        Rx.<x> = PolynomialRing(GF(p))
        Rxy.<x, y> = PolynomialRing(GF(p), 2)
        Fxy = FractionField(Rxy)
        self.polynomial = Rx(f)
        self.exponent = m
        self.characteristic = p
        
        r = Rx(f).degree()
        delta = GCD(r, m)
        self.degree_holo = degrees_holomorphic_differentials(f, m, p)
        self.degree_de_rham0 = degrees_de_rham0(f, m, p)
        self.degree_de_rham1 = degrees_de_rham1(f, m, p)
        
        holo_basis = holomorphic_differentials_basis(f, m, p)
        holo_basis_converted = []
        for a in holo_basis:
            holo_basis_converted += [superelliptic_form(self, a)]
        
        self.basis_holomorphic_differentials = holo_basis_converted
        

        dr_basis = de_rham_basis(f, m, p)
        dr_basis_converted = []
        for (a, b) in dr_basis:
            dr_basis_converted += [superelliptic_cech(self, superelliptic_form(self, a), superelliptic_function(self, b))]
        
        self.basis_de_rham = dr_basis_converted
        
    def __repr__(self):
        f = self.polynomial
        m = self.exponent
        p = self.characteristic
        return 'Superelliptic curve with the equation y^' + str(m) + ' = ' + str(f)+' over finite field with ' + str(p) + ' elements.'
    
    def is_smooth(self):
        f = self.polynomial
        if f.discriminant() == 0:
            return 0
        return 1
    
    def genus(self):
        r = self.polynomial.degree()
        m = self.exponent
        delta = GCD(r, m)
        return 1/2*((r-1)*(m-1) - delta + 1)
    
    def verschiebung_matrix(self):
        basis = self.basis_de_rham
        g = self.genus()
        p = self.characteristic
        M = matrix(GF(p), 2*g, 2*g)
        for i in range(0, len(basis)):
            w = basis[i]
            v = w.verschiebung().coordinates()
            M[i, :] = v
        return M
    
    def frobenius_matrix(self):
        basis = self.basis_de_rham
        g = self.genus()
        p = self.characteristic
        M = matrix(GF(p), 2*g, 2*g)
        
        for i in range(0, len(basis)):
            w = basis[i]
            v = w.frobenius().coordinates()
            M[i, :] = v
        return M

    def cartier_matrix(self):
        basis = self.basis_holomorphic_differentials
        g = self.genus()
        p = self.characteristic
        M = matrix(GF(p), g, g)
        for i in range(0, len(basis)):
            w = basis[i]
            v = w.cartier().coordinates()
            M[i, :] = v
        return M     
    
    def p_rank(self):
        return self.cartier_matrix().rank()
    
    def final_type(self, test = 0):
        F = self.frobenius_matrix()
        V = self.verschiebung_matrix()
        p = self.characteristic
        return flag(F, V, p, test)
    
def reduction(C, g):
    p = C.characteristic
    Rxy.<x, y> = PolynomialRing(GF(p), 2)
    Fxy = FractionField(Rxy)
    f = C.polynomial
    r = f.degree()
    m = C.exponent
    g = Fxy(g)
    g1 = g.numerator()
    g2 = g.denominator()
    
    Rx.<x> = PolynomialRing(GF(p))
    Fx = FractionField(Rx)
    FxRy.<y> = PolynomialRing(Fx)    
    (A, B, C) = xgcd(FxRy(g2), FxRy(y^m - f))
    g = FxRy(g1*B/A)
    
    while(g.degree(Rxy(y)) >= m):
        d = g.degree(Rxy(y))
        G = coff(g, d)
        i = floor(d/m)
        g = g - G*y^d + f^i * y^(d%m) *G
    
    return(FxRy(g))

def reduction_form(C, g):
    p = C.characteristic
    Rxy.<x, y> = PolynomialRing(GF(p), 2)
    Fxy = FractionField(Rxy)
    f = C.polynomial
    r = f.degree()
    m = C.exponent
    g = reduction(C, g)

    g1 = Rxy(0)
    Rx.<x> = PolynomialRing(GF(p))
    Fx = FractionField(Rx)
    FxRy.<y> = PolynomialRing(Fx)
    
    g = FxRy(g)
    for j in range(0, m):
        if j==0:
            G = coff(g, 0)
            g1 += FxRy(G)
        else:
            G = coff(g, j)
            g1 += Fxy(y^(j-m)*f*G)
    return(g1)
        
class superelliptic_function:
    def __init__(self, C, g):
        p = C.characteristic
        Rxy.<x, y> = PolynomialRing(GF(p), 2)
        Fxy = FractionField(Rxy)
        f = C.polynomial
        r = f.degree()
        m = C.exponent
        
        self.curve = C
        g = reduction(C, g)
        self.function = g
        
    def __repr__(self):
        return str(self.function)
    
    def jth_component(self, j):
        g = self.function
        C = self.curve
        p = C.characteristic
        Rx.<x> = PolynomialRing(GF(p))
        Fx.<x> = FractionField(Rx)
        FxRy.<y> = PolynomialRing(Fx)
        g = FxRy(g)
        return coff(g, j)
    
    def __add__(self, other):
        C = self.curve
        g1 = self.function
        g2 = other.function
        g = reduction(C, g1 + g2)
        return superelliptic_function(C, g)
    
    def __sub__(self, other):
        C = self.curve
        g1 = self.function
        g2 = other.function
        g = reduction(C, g1 - g2)
        return superelliptic_function(C, g)
    
    def __mul__(self, other):
        C = self.curve
        g1 = self.function
        g2 = other.function
        g = reduction(C, g1 * g2)
        return superelliptic_function(C, g)
    
    def __truediv__(self, other):
        C = self.curve
        g1 = self.function
        g2 = other.function
        g = reduction(C, g1 / g2)
        return superelliptic_function(C, g)
    
def diffn(self):
    C = self.curve
    f = C.polynomial
    m = C.exponent
    p = C.characteristic
    g = self.function
    Rxy.<x, y> = PolynomialRing(GF(p), 2)
    Fxy = FractionField(Rxy)
    g = Fxy(g)
    A = g.derivative(x)
    B = g.derivative(y)*f.derivative(x)/(m*y^(m-1))
    return superelliptic_form(C, A+B)
        
class superelliptic_form:
    def __init__(self, C, g):
        p = C.characteristic
        Rxy.<x, y> = PolynomialRing(GF(p), 2)
        Fxy = FractionField(Rxy)
        g = Fxy(reduction_form(C, g))
        self.form = g
        self.curve = C      
        
    def __add__(self, other):
        C = self.curve
        g1 = self.form
        g2 = other.form
        g = reduction(C, g1 + g2)
        return superelliptic_form(C, g)
    
    def __sub__(self, other):
        C = self.curve
        g1 = self.form
        g2 = other.form
        g = reduction(C, g1 - g2)
        return superelliptic_form(C, g)
    
    def __repr__(self):
        g = self.form
        if len(str(g)) == 1:
            return str(g) + ' dx'
        return '('+str(g) + ') dx'

    def __rmul__(self, constant):
        C = self.curve
        omega = self.form
        return superelliptic_form(C, constant*omega)        
    
    def cartier(self):
        C = self.curve
        m = C.exponent
        p = C.characteristic
        f = C.polynomial
        Rx.<x> = PolynomialRing(GF(p))
        Fx = FractionField(Rx)
        FxRy.<y> = PolynomialRing(Fx)
        Fxy = FractionField(FxRy)
        result = superelliptic_form(C, FxRy(0))
        mult_order = Integers(m)(p).multiplicative_order()
        M = Integer((p^(mult_order)-1)/m)
        
        for j in range(1, m):
            fct_j = self.jth_component(j)
            h = Rx(fct_j*f^(M*j))
            j1 = (p^(mult_order-1)*j)%m
            B = floor(p^(mult_order-1)*j/m)
            result += superelliptic_form(C, polynomial_part(p, h)/(f^B*y^(j1)))
        return result   
    
    def coordinates(self):
        C = self.curve
        p = C.characteristic
        m = C.exponent
        Rx.<x> = PolynomialRing(GF(p))
        Fx = FractionField(Rx)
        FxRy.<y> = PolynomialRing(Fx)
        g = C.genus()
        degrees_holo = C.degree_holo
        degrees_holo_inv = {b:a for a, b in degrees_holo.items()}
        basis = C.basis_holomorphic_differentials
        
        for j in range(1, m):
            omega_j = Fx(self.jth_component(j))
            if omega_j != Fx(0):
                d = degree_of_rational_fctn(omega_j, p)
                index = degrees_holo_inv[(d, j)]
                a = coeff_of_rational_fctn(omega_j, p)
                a1 = coeff_of_rational_fctn(basis[index].jth_component(j), p)
                elt = self - (a/a1)*basis[index]
                return elt.coordinates() + a/a1*vector([GF(p)(i == index) for i in range(0, g)])
            
        return vector(g*[0])
    
    def jth_component(self, j):
        g = self.form
        C = self.curve
        p = C.characteristic
        Rx.<x> = PolynomialRing(GF(p))
        Fx = FractionField(Rx)
        FxRy.<y> = PolynomialRing(Fx)
        Fxy = FractionField(FxRy)
        Ryinv.<y_inv> = PolynomialRing(Fx)
        g = Fxy(g)
        g = g(y = 1/y_inv)
        g = Ryinv(g)
        return coff(g, j)
    
    def is_regular_on_U0(self):
        C = self.curve
        p = C.characteristic
        m = C.exponent
        Rx.<x> = PolynomialRing(GF(p))
        for j in range(1, m):
            if self.jth_component(j) not in Rx:
                return 0
        return 1
    
    def is_regular_on_Uinfty(self):
        C = self.curve
        p = C.characteristic
        m = C.exponent
        f = C.polynomial
        r = f.degree()
        delta = GCD(m, r)
        M = m/delta
        R = r/delta
        
        for j in range(1, m):
            A = self.jth_component(j)
            d = degree_of_rational_fctn(A, p)
            if(-d*M + j*R -(M+1)<0):
                return 0
        return 1
    
    
class superelliptic_cech:
    def __init__(self, C, omega, fct):
        self.omega0 = omega
        self.omega8 = omega - diffn(fct)
        self.f = fct
        self.curve = C
        
    def __add__(self, other):
        C = self.curve
        return superelliptic_cech(C, self.omega0 + other.omega0, self.f + other.f)
    
    def __sub__(self, other):
        C = self.curve
        return superelliptic_cech(C, self.omega0 - other.omega0, self.f - other.f)

    def __rmul__(self, constant):
        C = self.curve
        w1 = self.omega0.form
        f1 = self.f.function
        w2 = superelliptic_form(C, constant*w1)
        f2 = superelliptic_function(C, constant*f1)
        return superelliptic_cech(C, w2, f2)    
    
    def __repr__(self):
        return "(" + str(self.omega0) + ", " + str(self.f) + ", " + str(self.omega8) + ")" 
    
    def verschiebung(self):
        C = self.curve
        omega = self.omega0
        p = C.characteristic
        Rx.<x> = PolynomialRing(GF(p))
        return superelliptic_cech(C, omega.cartier(), superelliptic_function(C, Rx(0)))
    
    def frobenius(self):
        C = self.curve
        fct = self.f.function
        p = C.characteristic
        Rx.<x> = PolynomialRing(GF(p))
        return superelliptic_cech(C, superelliptic_form(C, Rx(0)), superelliptic_function(C, fct^p))

    def coordinates(self):
        C = self.curve
        p = C.characteristic
        m = C.exponent
        Rx.<x> = PolynomialRing(GF(p))
        Fx = FractionField(Rx)
        FxRy.<y> = PolynomialRing(Fx)
        g = C.genus()
        degrees_holo = C.degree_holo
        degrees_holo_inv = {b:a for a, b in degrees_holo.items()}
        degrees0 = C.degree_de_rham0
        degrees0_inv = {b:a for a, b in degrees0.items()}
        degrees1 = C.degree_de_rham1
        degrees1_inv = {b:a for a, b in degrees1.items()}
        basis = C.basis_de_rham
        
        omega = self.omega0
        fct = self.f
        
        if fct.function == Rx(0) and omega.form != Rx(0):
            for j in range(1, m):
                omega_j = Fx(omega.jth_component(j))
                if omega_j != Fx(0):
                    d = degree_of_rational_fctn(omega_j, p)
                    index = degrees_holo_inv[(d, j)]
                    a = coeff_of_rational_fctn(omega_j, p)
                    a1 = coeff_of_rational_fctn(basis[index].omega0.jth_component(j), p)
                    elt = self - (a/a1)*basis[index]
                    return elt.coordinates() + a/a1*vector([GF(p)(i == index) for i in range(0, 2*g)])
                    
        for j in range(1, m):
            fct_j = Fx(fct.jth_component(j))
            if (fct_j != Rx(0)):
                d = degree_of_rational_fctn(fct_j, p)
            
                if (d, j) in degrees1.values():
                    index = degrees1_inv[(d, j)]
                    a = coeff_of_rational_fctn(fct_j, p)
                    elt = self - (a/m)*basis[index]
                    return elt.coordinates() + a/m*vector([GF(p)(i == index) for i in range(0, 2*g)])
                
                if d<0:
                    a = coeff_of_rational_fctn(fct_j, p)
                    h = superelliptic_function(C, FxRy(a*y^j*x^d))
                    elt = superelliptic_cech(C, self.omega0, self.f - h)
                    return elt.coordinates()
            
                if (fct_j != Rx(0)):
                    G = superelliptic_function(C, y^j*x^d)
                    a = coeff_of_rational_fctn(fct_j, p)
                    elt =self - a*superelliptic_cech(C, diffn(G), G)
                    return elt.coordinates()

        return vector(2*g*[0])
    
    def is_cocycle(self):
        w0 = self.omega0
        w8 = self.omega8
        fct = self.f
        if not w0.is_regular_on_U0() and not w8.is_regular_on_Uinfty():
            return('w0 & w8')
        if not w0.is_regular_on_U0():
            return('w0')
        if not w8.is_regular_on_Uinfty():
            return('w8')
        if w0.is_regular_on_U0() and w8.is_regular_on_Uinfty():
            return 1
        return 0
        
def degree_of_rational_fctn(f, p):
    Rx.<x> = PolynomialRing(GF(p))
    Fx = FractionField(Rx)
    f = Fx(f)
    f1 = f.numerator()
    f2 = f.denominator()
    d1 = f1.degree()
    d2 = f2.degree()
    return(d1 - d2)

def coeff_of_rational_fctn(f, p):
    Rx.<x> = PolynomialRing(GF(p))
    Fx = FractionField(Rx)
    f = Fx(f)
    if f == Rx(0):
        return 0
    f1 = f.numerator()
    f2 = f.denominator()
    d1 = f1.degree()
    d2 = f2.degree()
    a1 = f1.coefficients(sparse = false)[d1]
    a2 = f2.coefficients(sparse = false)[d2]
    return(a1/a2)

def coff(f, d):
    lista = f.coefficients(sparse = false)
    if len(lista) <= d:
        return 0
    return lista[d]

def cut(f, i):
    R = f.parent()
    coeff = f.coefficients(sparse = false)
    return sum(R(x^(j-i-1)) * coeff[j] for j in range(i+1, f.degree() + 1))

def polynomial_part(p, h):
    Rx.<x> = PolynomialRing(GF(p))
    h = Rx(h)
    result = Rx(0)
    for i in range(0, h.degree()+1):
        if (i%p) == p-1:
            power = Integer((i-(p-1))/p)
            result += Integer(h[i]) * x^(power)    
    return result

In [2]:
def preimage(U, V, M): #preimage of subspace U under M
    basis_preimage = M.right_kernel().basis()
    imageU = U.intersection(M.transpose().image())
    basis = imageU.basis()
    for v in basis:
        w = M.solve_right(v)
        basis_preimage = basis_preimage + [w]
    return V.subspace(basis_preimage)

def image(U, V, M):
    basis = U.basis()
    basis_image = []
    for v in basis:
        basis_image += [M*v]
    return V.subspace(basis_image)

def flag(F, V, p, test = 0):
    dim = F.dimensions()[0]
    space = VectorSpace(GF(p), dim)
    flag_subspaces = (dim+1)*[0]
    flag_used = (dim+1)*[0]
    final_type = (dim+1)*['?']
    
    flag_subspaces[dim] = space
    flag_used[dim] = 1
   
    
    while 1 in flag_used:
        index = flag_used.index(1)
        flag_used[index] = 0
        U = flag_subspaces[index]
        U_im = image(U, space, V)
        d_im = U_im.dimension()
        final_type[index] = d_im
        U_pre = preimage(U, space, F)
        d_pre = U_pre.dimension()
        
        if flag_subspaces[d_im] == 0:
            flag_subspaces[d_im] = U_im
            flag_used[d_im] = 1
        
        if flag_subspaces[d_pre] == 0:
            flag_subspaces[d_pre] = U_pre
            flag_used[d_pre] = 1
    
    if test == 1:
        print('(', final_type, ')')
    
    for i in range(0, dim+1):
        if final_type[i] == '?' and final_type[dim - i] != '?':
            i1 = dim - i
            final_type[i] = final_type[i1] - i1 + dim/2
    
    final_type[0] = 0
    
    for i in range(1, dim+1):
        if final_type[i] == '?':
            prev = final_type[i-1]
            if prev != '?' and prev in final_type[i+1:]:
                final_type[i] = prev
                
    for i in range(1, dim+1):
        if final_type[i] == '?':
            final_type[i] = min(final_type[i-1] + 1, dim/2)
    
    if is_final(final_type, dim/2):
        return final_type[1:dim/2 + 1]
    print('error:', final_type[1:dim/2 + 1])
    
def is_final(final_type, dim):
    n = len(final_type)
    if final_type[0] != 0:
        return 0
    
    if final_type[n-1] != dim:
        return 0
    
    for i in range(1, n):
        if final_type[i] != final_type[i - 1] and final_type[i] != final_type[i - 1] + 1:
            return 0
    return 1

In [3]:
from datetime import datetime

In [3]:
p = 5
R.<x> = PolynomialRing(GF(p))
f = x^3 + x + 1
m = 2
C = superelliptic(f, m, p)

In [7]:
C.basis_holomorphic_differentials[0].form

1/y

In [13]:
now = datetime.now()

current_time = now.strftime("%H:%M:%S")
print("Current Time =", current_time)

p = 17
Rx.<x> = PolynomialRing(GF(p))
C = superelliptic(x^13+x^8+x, 2, p)
print(C.final_type())

now = datetime.now()

current_time = now.strftime("%H:%M:%S")
print("Current Time =", current_time)

Current Time = 18:11:00
[1, 2, 3, 4, 5, 6]
Current Time = 18:11:21


In [15]:
def p_cov(C):
    m = C.exponent
    p = C.characteristic
    f = C.polynomial
    return superelliptic(f(x^p - x), m, p)

In [26]:
p = 3
Rx.<x> = PolynomialRing(GF(p))
C = superelliptic(2*x^9+x^8+x, 2, p)
C1 = p_cov(C)
print(C.final_type(), C1.final_type())

[1, 1, 2, 3] [1, 2, 3, 3, 4, 5, 6, 7, 8, 9, 10, 10, 11]


In [29]:
p = 5
Rx.<x> = PolynomialRing(GF(p))
C = superelliptic(x^9+x^8+x, 2, p)
C1 = p_cov(C)
print(C.final_type(1), C1.final_type(1))

( ['?', 1, 1, 2, 3, 3, 3, 4, 4] )
( ['?', '?', '?', '?', '?', 5, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, '?', 18, 19, 19, '?', 21, 21, 21, 21, 21, 21, 21, 21, 21, 21, 21, 21, 21, 21, 22, '?', '?', '?', '?', 22] )
[1, 1, 2, 3] [1, 2, 3, 4, 5, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 18, 18, 19]


In [24]:
C1.genus()

22

In [10]:
p = 11
for a in range(0, p):
    for b in range(0, p):
        for c in range(0, p):
            Rx.<x> = PolynomialRing(GF(p))
            C = superelliptic(x^9+a*x^8+c*x, 2, p)
            if C.is_smooth() and C.p_rank() == 3:
                M = C.cartier_matrix()
                print(C.polynomial, C.p_rank(), (M^4).rank(), 4 - (M-identity_matrix(4)).rank())
                V = C.verschiebung_matrix()
                F = C.frobenius_matrix()
                print(flag(F, V, p))

x^9 + x^8 + x 3 2 0
(( ['?', '?', 2, 2, 3, 3, 4, '?', 4] ))
[1, 2, 2, 3]
x^9 + x^8 + 2*x 3 2 0
(( ['?', '?', 2, 2, 3, 3, 4, '?', 4] ))
[1, 2, 2, 3]
x^9 + x^8 + 3*x 3 2 0
(( ['?', '?', 2, 2, 3, 3, 4, '?', 4] ))
[1, 2, 2, 3]
x^9 + x^8 + 4*x 3 2 0
(( ['?', '?', 2, 2, 3, 3, 4, '?', 4] ))
[1, 2, 2, 3]
x^9 + x^8 + 5*x 3 2 0
(( ['?', '?', 2, 2, 3, 3, 4, '?', 4] ))
[1, 2, 2, 3]
x^9 + x^8 + 6*x 3 2 0
(( ['?', '?', 2, 2, 3, 3, 4, '?', 4] ))
[1, 2, 2, 3]
x^9 + x^8 + 7*x 3 2 0
(( ['?', '?', 2, 2, 3, 3, 4, '?', 4] ))
[1, 2, 2, 3]
x^9 + x^8 + 8*x 3 0 0
(( [0, 0, 1, 2, 3, 3, 3, 3, 4] ))
[0, 1, 2, 3]
x^9 + x^8 + 9*x 3 2 0
(( ['?', '?', 2, 2, 3, 3, 4, '?', 4] ))
[1, 2, 2, 3]
x^9 + x^8 + x 3 2 0
(( ['?', '?', 2, 2, 3, 3, 4, '?', 4] ))
[1, 2, 2, 3]
x^9 + x^8 + 2*x 3 2 0
(( ['?', '?', 2, 2, 3, 3, 4, '?', 4] ))
[1, 2, 2, 3]
x^9 + x^8 + 3*x 3 2 0
(( ['?', '?', 2, 2, 3, 3, 4, '?', 4] ))
[1, 2, 2, 3]
x^9 + x^8 + 4*x 3 2 0
(( ['?', '?', 2, 2, 3, 3, 4, '?', 4] ))
[1, 2, 2, 3]
x^9 + x^8 + 5*x 3 2 0
(( ['?', '?',

KeyboardInterrupt: 

In [7]:
R.<x> = PolynomialRing(GF(13))
C = superelliptic(x^3+x, 2, 13)
print(C.basis_de_rham)

[((1/y) dx, 0, (1/y) dx), ((x/y) dx, 2/x*y, (1/(x*y)) dx)]


In [81]:
p = 5
Rx.<x> = PolynomialRing(GF(p))
C = superelliptic(x^3 - x, 2, p)
if (C.is_smooth()):
    print(C.p_rank())
    print(C.final_type())

1
[1]


In [58]:
C.frobenius_matrix()

[0 0 0 0 0 0 0 0]
[0 0 0 0 0 0 0 0]
[0 0 0 0 0 0 0 0]
[0 0 0 0 0 0 0 0]
[0 0 0 4 2 3 3 2]
[4 0 4 4 2 0 0 4]
[0 0 4 3 0 0 1 2]
[3 0 0 0 0 1 0 0]

In [62]:
flag(F, V, p)

test [0, -1, -1, -1, 4, -1, -1, -1, 4]
poprawiony ft [0, 1, 2, 3, 4, 4, 4, 4, 4]


[1, 2, 3, 4]

In [24]:
f = x^9+3*x^3+x^2+x+1
r = f.degree()
i = 2
j = 1
m = 2
print(Rx(m-j)*Rx(x)*Rx(f.derivative()))
print(Rx(m)*Rx(i)*f)

4*x^9 + 4*x^3 + 2*x^2 + x
4*x^9 + 2*x^3 + 4*x^2 + 4*x + 4


In [26]:
print(r*(m-j))
print(m*i)
print(f.derivative())

9
4
4*x^8 + 4*x^2 + 2*x + 1


In [31]:
x*f.derivative() - 2*2*f

2*x^3 + 3*x^2 + 2*x + 1

In [73]:
M = matrix(QQ, [[1,2], [3,6]])
U = M.kernel()
V = VectorSpace(QQ,2)
M.transpose().image()

Vector space of degree 2 and dimension 1 over Rational Field
Basis matrix:
[1 3]

In [77]:
l = U.basis()
l = l +[(1, 1/3)]

In [24]:
###fragment kodu do obliczania residuuow w niesk - zaniechany
#def more_v(f, prec):
#    C = f.curve
#    f = f.vw
#    g = C.polynomial8
#    p = C.characteristic
#    m = C.exponent
#    r = C.polynomial.degree()
#    delta, a, b = xgcd(m, r)
#    a = -a
#    M = m/delta
#    R = r/delta
#    
#    Fpbar = GF(p).algebraic_closure()
#    Ruv.<u, v> = PolynomialRing(Fpbar, 2)
#    if prec == 0:
#        return 0
#    zeta = Fpbar.zeta(m)
#    a = f(v = zeta, w = 0)
#    f1 = f - a
#    if w.divides(f1):
#        return more_v(f1/w, prec-1)
    

In [211]:
p = 7
Rx.<x> = PolynomialRing(GF(p))
C = superelliptic(x^3 + x + 3, 5, p)
baza = C.basis_de_rham
print(C.genus())
#E = EllipticCurve(GF(p), [1, 2])
print(E.trace_of_frobenius())
#C.basis_holomorphic_differentials(  )

4
2


In [212]:
C.degree_de_rham0

{0: (0, 2),
 1: (0, 3),
 2: (0, 4),
 3: (1, 4),
 4: (-1, 1),
 5: (0, 1),
 6: (1, 2),
 7: (1, 3)}

In [213]:
C.basis_de_rham

{0: ((1/y^2) dx, 0, (1/y^2) dx),
 1: ((1/y^3) dx, 0, (1/y^3) dx),
 2: ((1/y^4) dx, 0, (1/y^4) dx),
 3: ((x/y^4) dx, 0, (x/y^4) dx),
 4: (0 dx, 5/x*y^4, ((x + 1)/(x^2*y)) dx),
 5: ((2/y) dx, 5/x^2*y^4, ((-x + 2)/(x^3*y)) dx),
 6: (((-3*x)/y^2) dx, 5/x*y^3, ((2*x + 1)/(x^2*y^2)) dx),
 7: ((x/y^3) dx, 5/x*y^2, ((3*x + 1)/(x^2*y^3)) dx)}

In [214]:
A = C.frobenius_matrix()
B = C.verschiebung_matrix()

In [227]:
A.solve_right((0, 0, 0, 0, 4, 2, 5, 3))

(1, 0, 0, 4, 3, 0, 2, 0)

In [228]:
A*vector((1, 0, 0, 4, 3, 0, 2, 0))

(0, 0, 0, 0, 4, 2, 5, 3)

In [225]:
vector((1, 0, 0, 4, 5, 0, 0, 0)) - vector((0, 0, 0, 0, 2, 6, 5, 5))

(1, 0, 0, 4, 3, -6, -5, -5)

In [83]:
omega = diffn(superelliptic_function(C, y^2))

In [84]:
omega.jth_component(0)

3*x^2 + 1

In [85]:
R.<x, y> = PolynomialRing(GF(p), 2)
g1 = x^3*y^7 + x^2*y^9
g2 = x^2*y + y^6
R1.<x> = PolynomialRing(GF(p))
R2 = FractionField(R1)
R3.<y> = PolynomialRing(R2)

xgcd(R3(g1), R3(g2))[1]*R3(g1) + xgcd(R3(g1), R3(g2))[2]*R3(g2)

y

In [86]:
H = HyperellipticCurve(x^5 - x + 1)

In [40]:
H

Hyperelliptic Curve over Finite Field of size 5 defined by y^2 = x^5 + 4*x + 1

In [84]:
f = x^3 + x + 2

In [86]:
f.derivative(x)

-2*x^2 + 1

In [3]:
p = 5
R1.<x> = PolynomialRing(GF(p))
R2 = FractionField(R1)
R3.<y> = PolynomialRing(R2)
g = y^2/x + y/(x+1)    
g = 1/y+x/y^2

In [4]:
R3.<z> = PolynomialRing(R2)
g(y = 1/z)

x*z^2 + z

In [57]:
f

x^3 + x + 4

In [62]:
f.coefficient()

AttributeError: 'sage.rings.polynomial.polynomial_zmod_flint.Polynomial_zmod_flint' object has no attribute 'coefficient'

In [35]:
x^3+x+1

x^3 + x + 1

In [36]:
parent(x)

Symbolic Ring

In [37]:
R.<x> = PolynomialRing(GF(5))

In [39]:
R = (x^3+x).parent()

In [44]:
R.<x, y> = PolynomialRing(GF(5))
RR = FractionField(R)
A = RR(1/(x*y))

In [45]:
A.derivative(x)

(-1)/(x^2*y)

In [42]:
dict1 = {}
dict1[3] = 5
dict1[6] = 121

In [46]:
degrees1_inv = {b:a for a, b in dict1.items()}

In [47]:
degrees1_inv

{5: 3, 121: 6}

In [28]:
C

Superelliptic curve with the equation y^7 = x^3 + x + 2 over finite field with 5 elements.

In [29]:
basis = C.basis_de_rham()

In [32]:
basis.items()

dict_items([(0, ((x/y) dx, 2/x*y, ((x^3*y^5 - x^3 + x - 1)/(x^2*y^6)) dx)), (1, (((-1)/y) dx, 2/x^2*y, ((-x^3*y^5 + x^3 - 2*x - 2)/(x^3*y^6)) dx)), (2, (((-2*x)/y^2) dx, 2/x*y^2, ((-2*x^3*y^3 + x^3 - 1)/(x^2*y^5)) dx)), (3, ((1/y^2) dx, 2/x^2*y^2, ((x^3*y^3 - 2*x^3 + 2*x - 2)/(x^3*y^5)) dx)), (4, ((1/y^3) dx, 0, (1/y^3) dx)), (5, (0 dx, 2/x*y^3, ((-2*x^3 - x - 1)/(x^2*y^4)) dx)), (6, ((1/y^4) dx, 0, (1/y^4) dx)), (7, ((2*x/y^4) dx, 2/x*y^4, ((2*x^3 - 2*x*y - y)/(x^2*y^4)) dx)), (8, ((1/y^5) dx, 0, (1/y^5) dx)), (9, ((x/y^5) dx, 0, (x/y^5) dx)), (10, ((1/y^6) dx, 0, (1/y^6) dx)), (11, ((x/y^6) dx, 0, (x/y^6) dx))])

In [9]:
m = 9
r = 6
delta, a, b = xgcd(m, r)
a = -a
xgcd(9, 6)

(3, 1, -1)

In [10]:
b*r -a*m, delta

(3, 3)

In [11]:
Fpbar = GF(5).algebraic_closure()
z = Fpbar.zeta(7)

In [23]:
GF(5^6)(z)

TypeError: unable to coerce <class 'sage.rings.algebraic_closure_finite_field.AlgebraicClosureFiniteField_pseudo_conway_with_category.element_class'>

In [21]:
Integers(7)(5).multiplicative_order()

6

In [7]:
Rx.<x> = PolynomialRing(QQ)
f = sum((i+1)*x^i for i in range(0, 10))

In [8]:
cut(f, 5)

10*x^3 + 9*x^2 + 8*x + 7

In [9]:
f

10*x^9 + 9*x^8 + 8*x^7 + 7*x^6 + 6*x^5 + 5*x^4 + 4*x^3 + 3*x^2 + 2*x + 1

In [45]:
E = EllipticCurve(GF(2), [0,0,1,0,1])
print(E)
print(E.frobenius_polynomial())

Elliptic Curve defined by y^2 + y = x^3 + 1 over Finite Field of size 2
x^2 + 2


In [41]:
E

Elliptic Curve defined by y^2 + y = x^3 + x over Finite Field of size 2

x^2 + 2*x + 2

In [30]:
now = datetime.now()

current_time = now.strftime("%H:%M:%S")
print("Current Time =", current_time)

p = 17
Rx.<x> = PolynomialRing(GF(p))
C = superelliptic(x^19+x^8+x, 2, p)
print(C.final_type())

now = datetime.now()

current_time = now.strftime("%H:%M:%S")
print("Current Time =", current_time)

Current Time = 18:56:38
[1, 2, 3, 4, 5, 6, 7, 8, 9]
Current Time = 18:57:11


In [12]:
p = 7
R.<x> = PolynomialRing(GF(p))
f = x^3 + x + 1
m = 2
C = superelliptic(f, m, p)

In [13]:
C.basis_de_rham

[((1/y) dx, 0, (1/y) dx), ((x/y) dx, 2/x*y, ((x + 2)/(x^2*y)) dx)]

In [6]:
w = C.basis_de_rham[1]

In [10]:
w0 = w.f

In [9]:
w0.is_regular_on_U0()

1

In [11]:
diffn(w0)

((x^3 - x - 2)/(x^2*y)) dx

In [9]:
p = 7
R.<x> = PolynomialRing(GF(p))
d = 9
f = sum(x^i * (d+1-i) for i in range(0, d+1))
m = 2
C = superelliptic(f, m, p)

In [10]:
C.basis_de_rham

[((1/y) dx, 0, (1/y) dx),
 ((x/y) dx, 0, (x/y) dx),
 ((x^2/y) dx, 0, (x^2/y) dx),
 ((x^3/y) dx, 0, (x^3/y) dx),
 (((-2*x^6 + x^5 + 2*x^4 + x^3 - 2*x^2)/y) dx, 2/x*y, ((2*x - 1)/(x^2*y)) dx),
 (((-2*x^6 + x^5 + 2*x^4 + x^3 - 2*x^2)/y) dx, 2/x^2*y, ((2*x^2 - x - 2)/(x^3*y)) dx),
 (((3*x^5 - 3*x^4 + 3*x^3 + 2*x + 2)/y) dx, 2/x^3*y, ((-3*x^2 + 3*x - 3)/(x^4*y)) dx),
 (((x^4 - 3*x^2 - x - 1)/y) dx, 2/x^4*y, ((3*x^4 - x^2 + 3)/(x^5*y)) dx)]

In [17]:
p = 13
R.<x> = PolynomialRing(GF(p))
f = x^3 + x
m = 2
C = superelliptic(f, m, p)
C.basis_de_rham

[((1/y) dx, 0, (1/y) dx), ((x/y) dx, 2/x*y, (1/(x*y)) dx)]

In [10]:
R(f*f(1/x)*x^3).discriminant()

4

In [11]:
p = 19
R.<x> = PolynomialRing(GF(p))
f = x^3 + x + 1
m = 2
C = superelliptic(f, m, p)
C.basis_de_rham

[((1/y) dx, 0, (1/y) dx), ((x/y) dx, 2/x*y, ((x + 2)/(x^2*y)) dx)]

In [4]:
p = 3
R.<x> = PolynomialRing(GF(p))
f = x^3 -x
m = 2
C = superelliptic(f, m, p)
C.basis_de_rham

[((1/y) dx, 0, (1/y) dx), ((x/y) dx, 2/x*y, ((-1)/(x*y)) dx)]

In [7]:
R.<x, y> = PolynomialRing(GF(p), 2)
s = superelliptic_function(C, 2*y/(x*(x+1)))

In [9]:
diffn(s)

((-x^2 - x + 1)/(x^2*y + x*y)) dx

In [10]:
o1 = superelliptic_cech(C, superelliptic_form(C, (x+1)/y), superelliptic_function(C, 2*y/(x+1)))

In [11]:
o2 = superelliptic_cech(C, superelliptic_form(C, x/y), superelliptic_function(C, 2*y/x))

In [12]:
o3 = superelliptic_cech(C, superelliptic_form(C, 1/y), superelliptic_function(C, 0))

In [13]:
o4 = o1 - o2 - o3

In [14]:
o4

(0 dx, (1/(x^2 + x))*y, ((-x^2 - x + 1)/(x^2*y + x*y)) dx)